In [5]:
import torch
import numpy as np
import torchvision.datasets

In [6]:
# https://github.com/oval-group/dfw
from dfw import DFW
from dfw.losses import MultiClassHingeLoss

In [7]:
pwd

'C:\\Users\\Akshit Bhatia\\OneDrive - Blue Avenir GmbH\\sebestian thesis\\Gradient-Descent-Optimization-and-Multitask-Learning'

In [8]:
import torch.utils.data

In [9]:
import torchvision
from torchvision import datasets
from torchvision.transforms import ToTensor 
image_data_train = torchvision.datasets.MNIST(root='./',train=True,download=True,transform=ToTensor())
image_data_test = torchvision.datasets.MNIST(root='./',train=False,download=True,transform=ToTensor())

In [10]:
data_loader_train = torch.utils.data.DataLoader(image_data_train,
                                          batch_size=8,
                                          shuffle=True,
                                          )

data_loader_test = torch.utils.data.DataLoader(image_data_test,
                                          batch_size=8,
                                          shuffle=True,
                                          )

## step 1 implement a normal mini batch mnist pytorch implementation

In [11]:
import torch.nn as nn
from torch.autograd import Function

device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")

inpsiz = 784 
hidensiz = 512 
numclases = 10
numepchs = 4
bachsiz = 100
l_r = 0.001

class neural_network(nn.Module):
    def __init__(self, inpsiz, hidensiz, numclases):
        super(neural_network, self).__init__()
        self.flatten = nn.Flatten()
        self.linear_relu_stack = nn.Sequential(
            nn.Linear(28*28, 512),
            nn.ReLU(),
            nn.Linear(512, 512),
            nn.ReLU(),
            nn.Linear(512, 10)
        )
    def forward(self, x):
        x = self.flatten(x)
        logits = self.linear_relu_stack(x)
        return logits
    
modl = neural_network(inpsiz, hidensiz, numclases)
# loss = MultiClassHingeLoss()

loss = nn.CrossEntropyLoss()
# create DFW optimizer with learning rate of 0.1
# optim = DFW(modl.parameters(), eta=0.1)
optim = torch.optim.SGD(modl.parameters(), lr=1e-3)
# train(data_loader_train,modl,loss,optim)
# print(modl)

Using cpu device


In [12]:
data_loader_train.batch_size

8

In [22]:
## mini training on batches for normal pytorch mnist setup
def train(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    model.train()
    
    loss_list=[]
    
    for batch, (X, y) in enumerate(dataloader):
        # one X is a batch of 8 instances
        device = "cuda" if torch.cuda.is_available() else "cpu"
        X, y = X.to(device), y.to(device)

        # Compute prediction error
        pred = model(X)
        
        loss = loss_fn(pred, y)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step(lambda: float(loss))

        print(loss)
        print(loss.T)
        loss, current = loss.item(), batch * len(X)
        print(f"loss: {loss:>7f}  [{current:>5d}/{size:>5d}]")



In [23]:
def test(dataloader, model, loss_fn):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    model.eval()
    test_loss, correct = 0, 0
    with torch.no_grad():
        for X, y in dataloader:
            X, y = X.to(device), y.to(device)
            pred = model(X)
            test_loss += loss_fn(pred, y).item()
            correct += (pred.argmax(1) == y).type(torch.float).sum().item()
    test_loss /= num_batches
    correct /= size
    print(f"Test Error: \n Accuracy: {(100*correct):>0.1f}%, Avg loss: {test_loss:>8f} \n")

In [24]:
epochs = 5
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    train(data_loader_train, modl, loss, optim)
    test(data_loader_test, modl, loss)
print("Done!")

Epoch 1
-------------------------------
tensor(0.0406, grad_fn=<NllLossBackward0>)
tensor(0.0406, grad_fn=<PermuteBackward0>)
loss: 0.040553  [    0/60000]
tensor(0.0469, grad_fn=<NllLossBackward0>)
tensor(0.0469, grad_fn=<PermuteBackward0>)
loss: 0.046874  [    8/60000]
tensor(0.1207, grad_fn=<NllLossBackward0>)
tensor(0.1207, grad_fn=<PermuteBackward0>)
loss: 0.120681  [   16/60000]
tensor(0.3345, grad_fn=<NllLossBackward0>)
tensor(0.3345, grad_fn=<PermuteBackward0>)
loss: 0.334498  [   24/60000]
tensor(0.2911, grad_fn=<NllLossBackward0>)
tensor(0.2911, grad_fn=<PermuteBackward0>)
loss: 0.291063  [   32/60000]
tensor(0.0710, grad_fn=<NllLossBackward0>)
tensor(0.0710, grad_fn=<PermuteBackward0>)
loss: 0.070959  [   40/60000]
tensor(0.3038, grad_fn=<NllLossBackward0>)
tensor(0.3038, grad_fn=<PermuteBackward0>)
loss: 0.303812  [   48/60000]
tensor(0.3249, grad_fn=<NllLossBackward0>)
tensor(0.3249, grad_fn=<PermuteBackward0>)
loss: 0.324899  [   56/60000]
tensor(0.0665, grad_fn=<NllLossB

tensor(0.5428, grad_fn=<PermuteBackward0>)
loss: 0.542849  [  664/60000]
tensor(0.3255, grad_fn=<NllLossBackward0>)
tensor(0.3255, grad_fn=<PermuteBackward0>)
loss: 0.325474  [  672/60000]
tensor(0.3056, grad_fn=<NllLossBackward0>)
tensor(0.3056, grad_fn=<PermuteBackward0>)
loss: 0.305550  [  680/60000]
tensor(0.2940, grad_fn=<NllLossBackward0>)
tensor(0.2940, grad_fn=<PermuteBackward0>)
loss: 0.294026  [  688/60000]
tensor(0.1754, grad_fn=<NllLossBackward0>)
tensor(0.1754, grad_fn=<PermuteBackward0>)
loss: 0.175369  [  696/60000]
tensor(0.0513, grad_fn=<NllLossBackward0>)
tensor(0.0513, grad_fn=<PermuteBackward0>)
loss: 0.051327  [  704/60000]
tensor(0.2295, grad_fn=<NllLossBackward0>)
tensor(0.2295, grad_fn=<PermuteBackward0>)
loss: 0.229455  [  712/60000]
tensor(0.2237, grad_fn=<NllLossBackward0>)
tensor(0.2237, grad_fn=<PermuteBackward0>)
loss: 0.223683  [  720/60000]
tensor(1.0199, grad_fn=<NllLossBackward0>)
tensor(1.0199, grad_fn=<PermuteBackward0>)
loss: 1.019882  [  728/60000]

tensor(0.7431, grad_fn=<PermuteBackward0>)
loss: 0.743052  [ 1232/60000]
tensor(0.1724, grad_fn=<NllLossBackward0>)
tensor(0.1724, grad_fn=<PermuteBackward0>)
loss: 0.172421  [ 1240/60000]
tensor(0.1549, grad_fn=<NllLossBackward0>)
tensor(0.1549, grad_fn=<PermuteBackward0>)
loss: 0.154853  [ 1248/60000]
tensor(0.0437, grad_fn=<NllLossBackward0>)
tensor(0.0437, grad_fn=<PermuteBackward0>)
loss: 0.043670  [ 1256/60000]
tensor(0.3271, grad_fn=<NllLossBackward0>)
tensor(0.3271, grad_fn=<PermuteBackward0>)
loss: 0.327125  [ 1264/60000]
tensor(0.1904, grad_fn=<NllLossBackward0>)
tensor(0.1904, grad_fn=<PermuteBackward0>)
loss: 0.190434  [ 1272/60000]
tensor(0.1325, grad_fn=<NllLossBackward0>)
tensor(0.1325, grad_fn=<PermuteBackward0>)
loss: 0.132524  [ 1280/60000]
tensor(0.1909, grad_fn=<NllLossBackward0>)
tensor(0.1909, grad_fn=<PermuteBackward0>)
loss: 0.190856  [ 1288/60000]
tensor(0.1752, grad_fn=<NllLossBackward0>)
tensor(0.1752, grad_fn=<PermuteBackward0>)
loss: 0.175153  [ 1296/60000]

tensor(0.4983, grad_fn=<PermuteBackward0>)
loss: 0.498329  [ 1816/60000]
tensor(0.2217, grad_fn=<NllLossBackward0>)
tensor(0.2217, grad_fn=<PermuteBackward0>)
loss: 0.221652  [ 1824/60000]
tensor(0.4362, grad_fn=<NllLossBackward0>)
tensor(0.4362, grad_fn=<PermuteBackward0>)
loss: 0.436199  [ 1832/60000]
tensor(0.2414, grad_fn=<NllLossBackward0>)
tensor(0.2414, grad_fn=<PermuteBackward0>)
loss: 0.241411  [ 1840/60000]
tensor(0.5466, grad_fn=<NllLossBackward0>)
tensor(0.5466, grad_fn=<PermuteBackward0>)
loss: 0.546609  [ 1848/60000]
tensor(0.0407, grad_fn=<NllLossBackward0>)
tensor(0.0407, grad_fn=<PermuteBackward0>)
loss: 0.040659  [ 1856/60000]
tensor(0.5195, grad_fn=<NllLossBackward0>)
tensor(0.5195, grad_fn=<PermuteBackward0>)
loss: 0.519499  [ 1864/60000]
tensor(0.2779, grad_fn=<NllLossBackward0>)
tensor(0.2779, grad_fn=<PermuteBackward0>)
loss: 0.277871  [ 1872/60000]
tensor(0.5036, grad_fn=<NllLossBackward0>)
tensor(0.5036, grad_fn=<PermuteBackward0>)
loss: 0.503569  [ 1880/60000]

tensor(0.4901, grad_fn=<PermuteBackward0>)
loss: 0.490110  [ 2424/60000]
tensor(0.7132, grad_fn=<NllLossBackward0>)
tensor(0.7132, grad_fn=<PermuteBackward0>)
loss: 0.713164  [ 2432/60000]
tensor(0.2554, grad_fn=<NllLossBackward0>)
tensor(0.2554, grad_fn=<PermuteBackward0>)
loss: 0.255374  [ 2440/60000]
tensor(0.5020, grad_fn=<NllLossBackward0>)
tensor(0.5020, grad_fn=<PermuteBackward0>)
loss: 0.501984  [ 2448/60000]
tensor(0.2077, grad_fn=<NllLossBackward0>)
tensor(0.2077, grad_fn=<PermuteBackward0>)
loss: 0.207693  [ 2456/60000]
tensor(0.5222, grad_fn=<NllLossBackward0>)
tensor(0.5222, grad_fn=<PermuteBackward0>)
loss: 0.522175  [ 2464/60000]
tensor(0.4448, grad_fn=<NllLossBackward0>)
tensor(0.4448, grad_fn=<PermuteBackward0>)
loss: 0.444763  [ 2472/60000]
tensor(1.0583, grad_fn=<NllLossBackward0>)
tensor(1.0583, grad_fn=<PermuteBackward0>)
loss: 1.058263  [ 2480/60000]
tensor(0.1381, grad_fn=<NllLossBackward0>)
tensor(0.1381, grad_fn=<PermuteBackward0>)
loss: 0.138137  [ 2488/60000]

...

tensor(0.4794, grad_fn=<NllLossBackward0>)
tensor(0.4794, grad_fn=<PermuteBackward0>)
loss: 0.479353  [56776/60000]
tensor(0.4896, grad_fn=<NllLossBackward0>)
tensor(0.4896, grad_fn=<PermuteBackward0>)
loss: 0.489622  [56784/60000]
tensor(0.0323, grad_fn=<NllLossBackward0>)
tensor(0.0323, grad_fn=<PermuteBackward0>)
loss: 0.032288  [56792/60000]
tensor(0.1741, grad_fn=<NllLossBackward0>)
tensor(0.1741, grad_fn=<PermuteBackward0>)
loss: 0.174103  [56800/60000]
tensor(0.2030, grad_fn=<NllLossBackward0>)
tensor(0.2030, grad_fn=<PermuteBackward0>)
loss: 0.203017  [56808/60000]
tensor(0.7444, grad_fn=<NllLossBackward0>)
tensor(0.7444, grad_fn=<PermuteBackward0>)
loss: 0.744393  [56816/60000]
tensor(0.1749, grad_fn=<NllLossBackward0>)
tensor(0.1749, grad_fn=<PermuteBackward0>)
loss: 0.174936  [56824/60000]
tensor(1.5098, grad_fn=<NllLossBackward0>)
tensor(1.5098, grad_fn=<PermuteBackward0>)
loss: 1.509826  [56832/60000]
tensor(0.1195, grad_fn=<NllLossBackward0>)
tensor(0.1195, grad_fn=<Permu

tensor(0.0417, grad_fn=<PermuteBackward0>)
loss: 0.041681  [57464/60000]
tensor(0.0748, grad_fn=<NllLossBackward0>)
tensor(0.0748, grad_fn=<PermuteBackward0>)
loss: 0.074809  [57472/60000]
tensor(0.1921, grad_fn=<NllLossBackward0>)
tensor(0.1921, grad_fn=<PermuteBackward0>)
loss: 0.192119  [57480/60000]
tensor(0.1239, grad_fn=<NllLossBackward0>)
tensor(0.1239, grad_fn=<PermuteBackward0>)
loss: 0.123890  [57488/60000]
tensor(0.5411, grad_fn=<NllLossBackward0>)
tensor(0.5411, grad_fn=<PermuteBackward0>)
loss: 0.541118  [57496/60000]
tensor(0.1525, grad_fn=<NllLossBackward0>)
tensor(0.1525, grad_fn=<PermuteBackward0>)
loss: 0.152470  [57504/60000]
tensor(0.3921, grad_fn=<NllLossBackward0>)
tensor(0.3921, grad_fn=<PermuteBackward0>)
loss: 0.392074  [57512/60000]
tensor(0.0665, grad_fn=<NllLossBackward0>)
tensor(0.0665, grad_fn=<PermuteBackward0>)
loss: 0.066470  [57520/60000]
tensor(0.0897, grad_fn=<NllLossBackward0>)
tensor(0.0897, grad_fn=<PermuteBackward0>)
loss: 0.089699  [57528/60000]

tensor(0.2971, grad_fn=<PermuteBackward0>)
loss: 0.297132  [58160/60000]
tensor(0.2674, grad_fn=<NllLossBackward0>)
tensor(0.2674, grad_fn=<PermuteBackward0>)
loss: 0.267411  [58168/60000]
tensor(0.3863, grad_fn=<NllLossBackward0>)
tensor(0.3863, grad_fn=<PermuteBackward0>)
loss: 0.386293  [58176/60000]
tensor(0.2340, grad_fn=<NllLossBackward0>)
tensor(0.2340, grad_fn=<PermuteBackward0>)
loss: 0.234037  [58184/60000]
tensor(0.1403, grad_fn=<NllLossBackward0>)
tensor(0.1403, grad_fn=<PermuteBackward0>)
loss: 0.140341  [58192/60000]
tensor(0.0148, grad_fn=<NllLossBackward0>)
tensor(0.0148, grad_fn=<PermuteBackward0>)
loss: 0.014790  [58200/60000]
tensor(0.2061, grad_fn=<NllLossBackward0>)
tensor(0.2061, grad_fn=<PermuteBackward0>)
loss: 0.206148  [58208/60000]
tensor(0.1167, grad_fn=<NllLossBackward0>)
tensor(0.1167, grad_fn=<PermuteBackward0>)
loss: 0.116681  [58216/60000]
tensor(0.4252, grad_fn=<NllLossBackward0>)
tensor(0.4252, grad_fn=<PermuteBackward0>)
loss: 0.425200  [58224/60000]

tensor(0.1178, grad_fn=<NllLossBackward0>)
tensor(0.1178, grad_fn=<PermuteBackward0>)
loss: 0.117756  [58896/60000]
tensor(0.1779, grad_fn=<NllLossBackward0>)
tensor(0.1779, grad_fn=<PermuteBackward0>)
loss: 0.177926  [58904/60000]
tensor(0.0493, grad_fn=<NllLossBackward0>)
tensor(0.0493, grad_fn=<PermuteBackward0>)
loss: 0.049342  [58912/60000]
tensor(0.1992, grad_fn=<NllLossBackward0>)
tensor(0.1992, grad_fn=<PermuteBackward0>)
loss: 0.199205  [58920/60000]
tensor(0.6466, grad_fn=<NllLossBackward0>)
tensor(0.6466, grad_fn=<PermuteBackward0>)
loss: 0.646596  [58928/60000]
tensor(0.0693, grad_fn=<NllLossBackward0>)
tensor(0.0693, grad_fn=<PermuteBackward0>)
loss: 0.069303  [58936/60000]
tensor(0.1740, grad_fn=<NllLossBackward0>)
tensor(0.1740, grad_fn=<PermuteBackward0>)
loss: 0.173951  [58944/60000]
tensor(0.0180, grad_fn=<NllLossBackward0>)
tensor(0.0180, grad_fn=<PermuteBackward0>)
loss: 0.018049  [58952/60000]
tensor(0.0845, grad_fn=<NllLossBackward0>)
tensor(0.0845, grad_fn=<Permu

tensor(0.4327, grad_fn=<PermuteBackward0>)
loss: 0.432724  [59576/60000]
tensor(0.6223, grad_fn=<NllLossBackward0>)
tensor(0.6223, grad_fn=<PermuteBackward0>)
loss: 0.622279  [59584/60000]
tensor(0.1055, grad_fn=<NllLossBackward0>)
tensor(0.1055, grad_fn=<PermuteBackward0>)
loss: 0.105476  [59592/60000]
tensor(0.0725, grad_fn=<NllLossBackward0>)
tensor(0.0725, grad_fn=<PermuteBackward0>)
loss: 0.072488  [59600/60000]
tensor(0.1383, grad_fn=<NllLossBackward0>)
tensor(0.1383, grad_fn=<PermuteBackward0>)
loss: 0.138280  [59608/60000]
tensor(0.1739, grad_fn=<NllLossBackward0>)
tensor(0.1739, grad_fn=<PermuteBackward0>)
loss: 0.173906  [59616/60000]
tensor(0.0615, grad_fn=<NllLossBackward0>)
tensor(0.0615, grad_fn=<PermuteBackward0>)
loss: 0.061483  [59624/60000]
tensor(0.0869, grad_fn=<NllLossBackward0>)
tensor(0.0869, grad_fn=<PermuteBackward0>)
loss: 0.086885  [59632/60000]
tensor(0.0635, grad_fn=<NllLossBackward0>)
tensor(0.0635, grad_fn=<PermuteBackward0>)
loss: 0.063450  [59640/60000]

## Step 2: store loss in a tensor

In [15]:
## training on batches
def train(dataloader, model, loss_fn, optimizer):
    size = len(dataloader.dataset)
    model.train()
    
    loss_list=[]
    
    for batch, (X, y) in enumerate(dataloader):
        # one X is a batch of 8 instances
        X, y = X.to(device), y.to(device)

        # Compute prediction error
        pred = model(X)
        
        loss = loss_fn(pred, y)
        loss_list.append(loss)
    tensor_list=torch.tensor(loss_list)
    tensor_list.backward()
# #     Backpropagation of all batches together
    optimizer.zero_grad()
    
    optimizer.step()


    loss, current = loss.item(), batch * len(X)
    print(f"loss: {loss:>7f}  [{current:>5d}/{size:>5d}]")



In [16]:
def test(dataloader, model, loss_fn):
    size = len(dataloader.dataset)
    num_batches = len(dataloader)
    model.eval()
    test_loss, correct = 0, 0
    with torch.no_grad():
        for X, y in dataloader:
            X, y = X.to(device), y.to(device)
            pred = model(X)
            test_loss += loss_fn(pred, y).item()
            correct += (pred.argmax(1) == y).type(torch.float).sum().item()
    test_loss /= num_batches
    correct /= size
    print(f"Test Error: \n Accuracy: {(100*correct):>0.1f}%, Avg loss: {test_loss:>8f} \n")

In [17]:
epochs = 1
for t in range(epochs):
    print(f"Epoch {t+1}\n-------------------------------")
    train(data_loader_train, modl, loss, optim)
#     test(data_loader_test, modl, loss)
print("Done!")

Epoch 1
-------------------------------


KeyboardInterrupt: 

In [15]:

nttlstps = len(data_loader_train)

for epoch in range(10):
    for bachsiz, (imgs,lbls) in enumerate(data_loader_train):
        imgs=imgs.reshape(-1,28*28)
        labls=lbls
        
        outp=modl(imgs)
        losses=loss(outp,lbls)
        optimizer.zero_grad()
        losses.backward()
        optimizer.step(lambda: float(losses))
    if((x+1)%100 == 0):
    
        print (f'Epochs [{epoch+1}/{numepchs}], Step[{x+1}/{nttlstps}], Losses: {losses.item():.4f}')


# # DFW can be used with standard pytorch syntax
# optimizer.zero_grad()
# loss = svm(model(x), y)
# loss.backward()
# # NB: DFW needs to have access to the current loss value,
# # (this syntax is compatible with standard pytorch optimizers too)
# optimizer.step(lambda: float(loss))

Epochs [1/4], Step[15000/15000], Losses: 0.4618
Epochs [2/4], Step[15000/15000], Losses: 0.0000
Epochs [3/4], Step[15000/15000], Losses: 0.0000
Epochs [4/4], Step[15000/15000], Losses: 0.0000
Epochs [5/4], Step[15000/15000], Losses: 0.0000
Epochs [6/4], Step[15000/15000], Losses: 0.0000
Epochs [7/4], Step[15000/15000], Losses: 0.0000
Epochs [8/4], Step[15000/15000], Losses: 0.1499
Epochs [9/4], Step[15000/15000], Losses: 0.0000
Epochs [10/4], Step[15000/15000], Losses: 0.0000


In [20]:
def accuracy(out, targets, topk=1):
    if topk == 1:
        _, pred = torch.max(out, 1)
        acc = torch.mean(torch.eq(pred, targets).float())
    else:
        _, pred = out.topk(topk, 1, True, True)
        pred = pred.t()
        correct = pred.eq(targets.view(1, -1).expand_as(pred))
        acc = correct[:topk].view(-1).float().sum(0) / out.size(0)

    return 100. * acc

In [23]:
for x, (imgs,lbls) in enumerate(data_loader_test):
        imgs=imgs.reshape(-1,28*28)
        labls=lbls
        
        outp=modl(imgs)
#         print(accuracy(outp,labls))
        print(loss(outp,labls))

tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.4742, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.4302, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1983, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2858, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tens

tensor(0.0269, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.4473, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0499, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0610, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2477, grad_fn=<DivBackward0>)
tensor(0.2753, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0006, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBack

tensor(0.0218, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1782, grad_fn=<DivBackward0>)
tensor(0.1320, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(1.0246, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0364, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.4454, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0225, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1144, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<Div

tensor(0.3261, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1187, grad_fn=<DivBackward0>)
tensor(0.1970, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2321, grad_fn=<DivBackward0>)
tensor(0.0986, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0960, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.9822, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBack

tensor(0.0079, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0292, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.3005, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0364, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.3967, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1627, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward

tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.4128, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.5002, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.3597, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2327, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2074, grad_fn=<DivBackward0>)


tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2843, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1199, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0210, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0382, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.1696, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)


tensor(0.1986, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0615, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0296, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0492, grad_fn=<DivBackward0>)
tens

tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.0287, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.2517, grad_fn=<DivBackward0>)
tensor(0.5176, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0.4134, grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tensor(0., grad_fn=<DivBackward0>)
tens

In [18]:
abs(-1)

1

In [ ]:
# convert the algorithm from paper: MTLearning as multi objective into code

import numpy as np

def aggregated_loss(alpha, tasks, gradient_task):
    """
    add the loss weighted with parameters extracted from frank wolfe method.
    
    Parameters:
        alpha: factors that frank wolfe method returns: array
        tasks: number of tasks: int
        gradient_task: gradient of the loss for each specific task
        
    Returns:
        returns the total loss as mentioned in the algorithm 2, step 5.
    """
    loss=0
    for t in range(tasks):
        loss+=alpha[t]*gradient_tasks[t]
    return loss


def get_rho(w,w_s):
    """
    Parameters
    ----------
        w: weight for each task
        w_s: shared weight
    Returns
    -------
        rho: Algorithm 1: (w_s-w)*w
    
    """
    if w.T*w_s >= w.T*w:
        rho=1
    elif w.T*w_s >= w_s.T*w_s:
        rho=0
    else:
        rho=((w_s-w).T*w_s)/abs((w-w_s)*(w-w_s))
    return rho

def frank_wolfe_solver(tasks, grad_t, rho):
    """
    based on procedure in algorithm 2
    
    
    """
    alpha=[1/tasks]*tasks  # step 7
    M=np.ndarray(shape=(tasks,tasks))  # will in step 8, M_{1,2} == M_{2,1}?
    for task_i in range(tasks):
        for task_j in range(tasks):
            M[task_i][task_j] = grad_t[task_i].T * grad_t[task_j]
    while rho < -0.5 or rho > 0.5 or count < iteration_limit-1:  # step 13
        min_value=100000
        task_index=1000
        for r in range(len(M)):
            value=0
            
            for t in range(len(M)):
                value += alpha[t]*M[r][t]  # refer to step 10 of algor 2
                
            if value<min_value:  # argmin in step 10 of algor 2
                min_value=value
                task_index=r
                
        chosen_task = task_index
        
        
        # now step 11 just like above
        
        
        
        chosen_task = arg_min(M, alpha)
        chosen_rho = arg_min((1-rho)*alpha + rho*e).T *  # step 11
        alpha = (1-chosen_rho)*alpha + chosen_rho * e
        
        return alpha

        
def optimizer(w_t, w_s, tasks,learning_rate,grad_t):
    '''
    Update the parameters based on algorithm 2.
    
    Parameters:
        w_s: shared weights
        w_t: task specific weight, an array with each element corresponding to each task
        tasks: number of tasks: int
        learning_rate: float
        grad_t: gradient of the loss for the specific task
        
    Returns:
        returns the updated shared weight.
    '''
    rho=[0]*len(w_t)
    for t in range(tasks):
        w_t[t] = w_t[t]-learning_rate*grad_t  # step 2
        rho[t] = get_rho(w_t[t],w_s)
    alpha=frank_wolfe_solver(w_t, w_s, rho)  # step 4
    w_s=w_s-learning_rate*aggregated_loss(alpha, tasks, grad_t)  # step 5
    
    return w_s
    
    
    

tasks = 100

loss

for t in tasks:
    